In [1]:
import os
import csv
import time
import socket
import logging
import statistics
import requests
import pandas as pd
from datetime import datetime
from urllib.parse import urlparse

In [2]:
logging.basicConfig(
    level=logging.INFO,
    format='%(asctime)s - %(levelname)s - %(message)s'
)

In [3]:
class SpeedTester:
    def __init__(self, num_requests=3):
        self.num_requests = num_requests
        self.unreachable_sites = []
        self.results_file = 'speed_test_results.csv'
        self._initialize_results_file()

    def _initialize_results_file(self):
        if not os.path.exists(self.results_file):
            with open(self.results_file, 'w', newline='') as f:
                writer = csv.DictWriter(f, fieldnames=['url', 'timestamp', 'dns_lookup', 'connection', 'ttfb', 'download', 'total', 'status', 'error_message'])
                writer.writeheader()

    def _read_tested_sites(self):
        if os.path.exists(self.results_file):
            with open(self.results_file, 'r') as f:
                reader = csv.DictReader(f)
                return {row['url']: row['status'] for row in reader}
        return {}

    def is_website_reachable(self, url):
        headers = {
            "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36"
        }

        try:
            response = requests.head(url, headers=headers, timeout=10, allow_redirects=True)
            return 200 <= response.status_code < 400
        except requests.RequestException as e:
            logging.warning(f"Website {url} unreachable: {e}")
            return False

    def _measure_dns(self, domain):
        start_time = time.time()
        try:
            socket.gethostbyname(domain)
            dns_time = time.time() - start_time
            return dns_time, True, ''
        except Exception as e:
            return None, False, str(e)

    def _test_single_url(self, url):
        logging.info(f"Starting test for {url}")

        metrics = {
            'url': url,
            'timestamp': datetime.now().isoformat(),
            'dns_lookup': [],
            'connection': [],
            'ttfb': [],
            'download': [],
            'total': [],
            'status': 'success',
            'error_message': ''
        }

        if not self.is_website_reachable(url):
            metrics['status'] = 'failed'
            metrics['error_message'] = 'Website unreachable'
            self.unreachable_sites.append({'url': url, 'error': 'Website unreachable'})
            return metrics

        parsed_url = urlparse(url)
        domain = parsed_url.netloc

        dns_time, dns_success, dns_error = self._measure_dns(domain)
        if not dns_success:
            metrics['status'] = 'failed'
            metrics['error_message'] = dns_error
            self.unreachable_sites.append({'url': url, 'error': dns_error})
            return metrics

        logging.info(f"Starting {self.num_requests} requests for {url}")
        for i in range(self.num_requests):
            logging.info(f"Request {i + 1}/{self.num_requests} for {url}")
            try:
                headers = {
                    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36"
                }

                metrics['dns_lookup'].append(dns_time)
                start_time = time.time()

                with requests.Session() as session:
                    conn_start = time.time()
                    response = session.get(url, headers=headers, stream=True, timeout=10, verify=False, allow_redirects=True)
                    conn_time = time.time() - conn_start

                    if not (200 <= response.status_code < 400):
                        raise requests.RequestException(f"Invalid status code: {response.status_code}")

                    end_time = time.time()
                    total_time = end_time - start_time
                    download_time = total_time - conn_time

                    metrics['connection'].append(conn_time)
                    metrics['download'].append(download_time)
                    metrics['total'].append(total_time)
                    metrics['ttfb'].append(response.elapsed.total_seconds())

                time.sleep(1)

            except Exception as e:
                logging.error(f"Error during request {i + 1} for {url}: {str(e)}")
                if i == 0:
                    metrics['status'] = 'failed'
                    metrics['error_message'] = str(e)
                    self.unreachable_sites.append({'url': url, 'error': str(e)})
                    break

        for key in ['dns_lookup', 'connection', 'ttfb', 'download', 'total']:
            if metrics[key]:
                metrics[key] = statistics.mean(metrics[key])
            else:
                metrics[key] = None

        logging.info(f"Completed testing {url}")

        with open(self.results_file, 'a', newline='') as f:
            writer = csv.DictWriter(f, fieldnames=['url', 'timestamp', 'dns_lookup', 'connection', 'ttfb', 'download', 'total', 'status', 'error_message'])
            writer.writerow(metrics)

        return metrics

    def test_urls(self, urls):
        results = []
        tested_sites = self._read_tested_sites()
        
        for url in urls:
            if tested_sites.get(url) == 'success':
                logging.info(f"Skipping {url}, already tested successfully.")
                continue
            result = self._test_single_url(url)
            results.append(result)
        
        return pd.DataFrame(results)

In [4]:
def main():
    try:
        logging.info("Starting speed test script")
        
        # Load websites from CSV and format URLs
        websites = pd.read_csv("../data/us_gov_domain_list.csv", usecols=["Domain name"]).drop_duplicates()
        websites = websites["Domain name"].dropna().astype(str).tolist()
        
        # Add https:// to URLs that don't have a scheme
        websites = ['https://' + site if not site.startswith(('http://', 'https://')) else site 
                   for site in websites]
        
        # Initialize tester and run tests
        tester = SpeedTester(num_requests=3)
        results_df = tester.test_urls(websites)
        
        # Print summary
        print("\nResults Summary:")
        print(f"Total sites tested: {len(websites)}")
        print(f"Successful: {len(results_df[results_df['status'] == 'success'])}")
        print(f"Failed: {len(results_df[results_df['status'] == 'failed'])}")
        
        # Print detailed results
        print("\nDetailed Results (in seconds):")
        display_columns = ['url', 'status', 'error_message'] + [
            col for col in results_df.columns 
            if col not in ['url', 'status', 'error_message', 'timestamp']
        ]
        print(results_df[display_columns].round(3))
        
    except Exception as e:
        logging.error(f"Script error: {str(e)}")
        print(f"Error: {str(e)}")

if __name__ == "__main__":
    main()

2025-01-27 20:13:35,104 - INFO - Starting speed test script
2025-01-27 20:13:35,160 - INFO - Skipping https://36thdistrictcourtmi.gov, already tested successfully.
2025-01-27 20:13:35,161 - INFO - Starting test for https://59dcmi.gov
2025-01-27 20:13:35,198 - WARNING - Website https://59dcmi.gov unreachable: HTTPSConnectionPool(host='59dcmi.gov', port=443): Max retries exceeded with url: / (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x7fa1fb3d1fd0>: Failed to establish a new connection: [Errno 8] nodename nor servname provided, or not known'))
2025-01-27 20:13:35,198 - INFO - Starting test for https://abbevillecitymarshal.gov
2025-01-27 20:13:35,578 - WARNING - Certificate did not match expected hostname: abbevillecitymarshal.gov. Certificate: {'subject': ((('commonName', '*.bizland.com'),),), 'issuer': ((('countryName', 'GB'),), (('stateOrProvinceName', 'Greater Manchester'),), (('localityName', 'Salford'),), (('organizationName', 'Sectigo Limited'),),

2025-01-27 20:13:49,474 - INFO - Skipping https://albanyny.gov, already tested successfully.
2025-01-27 20:13:49,474 - INFO - Skipping https://albanyoregon.gov, already tested successfully.
2025-01-27 20:13:49,474 - INFO - Starting test for https://albemarlenc.gov
2025-01-27 20:13:49,855 - INFO - Skipping https://alberttwpmi.gov, already tested successfully.
2025-01-27 20:13:49,856 - INFO - Starting test for https://albertvillemn.gov
2025-01-27 20:13:50,389 - INFO - Starting test for https://albuquerque-nm.gov
2025-01-27 20:14:00,417 - WARNING - Website https://albuquerque-nm.gov unreachable: HTTPSConnectionPool(host='albuquerque-nm.gov', port=443): Max retries exceeded with url: / (Caused by ConnectTimeoutError(<urllib3.connection.HTTPSConnection object at 0x7fa1fb51f670>, 'Connection to albuquerque-nm.gov timed out. (connect timeout=10)'))
2025-01-27 20:14:00,420 - INFO - Skipping https://aldanpa.gov, already tested successfully.
2025-01-27 20:14:00,421 - INFO - Skipping https://aled

2025-01-27 20:14:32,415 - WARNING - Website https://alpharettaga.gov unreachable: HTTPSConnectionPool(host='alpharettaga.gov', port=443): Max retries exceeded with url: / (Caused by SSLError(CertificateError("hostname 'alpharettaga.gov' doesn't match either of 'www.alpharetta.ga.us', 'alpharetta.ga.us'")))
2025-01-27 20:14:32,418 - INFO - Skipping https://alpineut.gov, already tested successfully.
2025-01-27 20:14:32,419 - INFO - Skipping https://alpinewy.gov, already tested successfully.
2025-01-27 20:14:32,420 - INFO - Starting test for https://alsteadnh.gov
2025-01-27 20:14:32,453 - WARNING - Website https://alsteadnh.gov unreachable: HTTPSConnectionPool(host='alsteadnh.gov', port=443): Max retries exceeded with url: / (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x7fa1fb51f700>: Failed to establish a new connection: [Errno 8] nodename nor servname provided, or not known'))
2025-01-27 20:14:32,455 - INFO - Skipping https://altavistava.gov, already tes

2025-01-27 20:14:33,608 - INFO - Starting test for https://andrewsnc.gov
2025-01-27 20:14:33,971 - WARNING - Website https://andrewsnc.gov unreachable: HTTPSConnectionPool(host='andrewsnc.gov', port=443): Max retries exceeded with url: / (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: certificate has expired (_ssl.c:1129)')))
2025-01-27 20:14:33,972 - INFO - Skipping https://angelfirenm.gov, already tested successfully.
2025-01-27 20:14:33,973 - INFO - Starting test for https://angelscamp.gov
2025-01-27 20:14:34,300 - WARNING - Website https://angelscamp.gov unreachable: ('Connection aborted.', RemoteDisconnected('Remote end closed connection without response'))
2025-01-27 20:14:34,300 - INFO - Skipping https://ankenyiowa.gov, already tested successfully.
2025-01-27 20:14:34,301 - INFO - Skipping https://annapolis.gov, already tested successfully.
2025-01-27 20:14:34,301 - INFO - Starting test for https://annapolismd.gov
2025

2025-01-27 20:14:47,053 - INFO - Skipping https://ardmoreok.gov, already tested successfully.
2025-01-27 20:14:47,055 - INFO - Skipping https://ardsleyvillage.gov, already tested successfully.
2025-01-27 20:14:47,060 - INFO - Skipping https://argentinetownship.gov, already tested successfully.
2025-01-27 20:14:47,066 - INFO - Skipping https://argonnewi.gov, already tested successfully.
2025-01-27 20:14:47,069 - INFO - Skipping https://argosin.gov, already tested successfully.
2025-01-27 20:14:47,072 - INFO - Skipping https://arkadelphia.gov, already tested successfully.
2025-01-27 20:14:47,076 - INFO - Skipping https://arkansascityks.gov, already tested successfully.
2025-01-27 20:14:47,077 - INFO - Starting test for https://arkomaok.gov
2025-01-27 20:14:47,125 - WARNING - Website https://arkomaok.gov unreachable: HTTPSConnectionPool(host='arkomaok.gov', port=443): Max retries exceeded with url: / (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x7fa1e003c7

...

2025-01-28 07:03:54,313 - INFO - Request 1/3 for https://ukb-nsn.gov
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'ukb-nsn.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.ukb-nsn.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
2025-01-28 07:03:55,901 - INFO - Request 2/3 for https://ukb-nsn.gov
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'ukb-nsn.gov'. Adding certificate verification is 

2025-01-28 07:04:26,601 - INFO - Request 1/3 for https://wakpamnilake-nsn.gov
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'wakpamnilake-nsn.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.wakpamnilake-nsn.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
2025-01-28 07:04:27,902 - INFO - Request 2/3 for https://wakpamnilake-nsn.gov
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'wakpamnilake-

2025-01-28 07:04:45,607 - INFO - Request 2/3 for https://yakamafish-nsn.gov
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'yakamafish-nsn.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
2025-01-28 07:04:46,794 - INFO - Request 3/3 for https://yakamafish-nsn.gov
/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'yakamafish-nsn.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
2025-01-28 07:04:48,017 - INFO - Completed testing https://yakamafish-nsn.gov
2025-01-28 07:04:48,025 - INFO - Starting test for https://yakamanation-nsn.gov
2025-01-28 07:04:48,226 - WA

/Users/soodoku/opt/anaconda3/lib/python3.9/site-packages/urllib3/connectionpool.py:1045: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www.kbic-nsn.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/1.26.x/advanced-usage.html#ssl-warnings
  warnings.warn(
2025-01-28 07:05:16,976 - INFO - Completed testing https://kbic-nsn.gov
2025-01-28 07:05:16,984 - INFO - Starting test for https://keweenawbay-nsn.gov
2025-01-28 07:05:17,084 - WARNING - Website https://keweenawbay-nsn.gov unreachable: HTTPSConnectionPool(host='keweenawbay-nsn.gov', port=443): Max retries exceeded with url: / (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x7fa1fb42fdf0>: Failed to establish a new connection: [Errno 8] nodename nor servname provided, or not known'))
2025-01-28 07:05:17,086 - INFO - Starting test for https://lummiswd.gov
2025-01-28 07:05:17,247 - INFO - Starting 3 requests for https://lummiswd.gov
202


Results Summary:
Total sites tested: 12047
Successful: 2353
Failed: 4717

Detailed Results (in seconds):
                                   url   status        error_message  \
0                   https://59dcmi.gov   failed  Website unreachable   
1     https://abbevillecitymarshal.gov   failed  Website unreachable   
2               https://aberdeenmd.gov   failed  Website unreachable   
3               https://abingtonpa.gov   failed  Website unreachable   
4           https://abitaspringsla.gov   failed  Website unreachable   
...                                ...      ...                  ...   
7065            https://29palmstcc.gov   failed  Website unreachable   
7066    https://fortsillapache-nsn.gov  success                        
7067              https://kbic-nsn.gov  success                        
7068       https://keweenawbay-nsn.gov   failed  Website unreachable   
7069              https://lummiswd.gov  success                        

     dns_lookup connection   

In [5]:
results_df = pd.read_csv("speed_test_results.csv")
results_df.head()

url                   timestamp  dns_lookup  \
0  https://36thdistrictcourtmi.gov  2025-01-26T19:40:17.997191    0.002886   
1           https://aberdeenwa.gov  2025-01-26T19:40:24.975568    0.001622   
2            https://abilenetx.gov  2025-01-26T19:40:31.094032    0.002446   
3          https://abingdon-va.gov  2025-01-26T19:40:37.745238    0.001519   
4           https://abingtonma.gov  2025-01-26T19:40:41.834491    0.003522   

   connection      ttfb  download     total   status error_message  
0    0.835984  0.416365  0.000344  0.836328  success           NaN  
1    0.740946  0.732713  0.000360  0.741307  success           NaN  
2    0.871456  0.862778  0.000340  0.871796  success           NaN  
3    0.264327  0.257977  0.000255  0.264582  success           NaN  
4    0.469036  0.140640  0.001009  0.470045  success           NaN

In [6]:
success_df = results_df[results_df['status'] == 'success']

speed_stats = success_df[['dns_lookup', 'connection', 'ttfb', 'download', 'total']].describe([.25, .75, .9, .95])
print("\nSpeed Statistics (in seconds):")
print(speed_stats)

success_rate = (len(success_df) / len(results_df)) * 100
print(f"\nSuccess Rate: {success_rate:.2f}%")


Speed Statistics (in seconds):
        dns_lookup   connection         ttfb     download        total
count  7330.000000  7330.000000  7330.000000  7330.000000  7330.000000
mean      0.002298     0.819048     0.623257     0.000292     0.819340
std       0.013605     7.082584     6.701383     0.000321     7.082585
min       0.000617     0.047352     0.010690     0.000062     0.047515
25%       0.001381     0.324867     0.185228     0.000228     0.325122
50%       0.001917     0.513076     0.364752     0.000277     0.513279
75%       0.002219     0.756509     0.563863     0.000328     0.756742
90%       0.002703     1.206231     0.929523     0.000401     1.206393
95%       0.002848     1.682465     1.422230     0.000422     1.682703
max       0.616600   356.858452   356.842515     0.019944   356.858677

Success Rate: 99.76%


### Let's compare these metrics to top 500 most visited websites